# Indonesian Document Retrieval System
**Objective:** Build a search engine capable of reading .txt, .pdf, and .docx files, processing Indonesian text using the Enhanced Confix Stripping (ECS) algorithm, and retrieving documents using the Vector Space Model (TF-IDF) and Cosine Similarity.

**Key Technologies:**
1.  **Text Processing:** Case Folding, Tokenization, Stopword Removal.
2.  **Stemming:** Sastrawi Library (Implementation of ECS algorithm).
3.  **Model:** Vector Space Model (VSM).
4.  **Weighting:** TF-IDF (Term Frequency - Inverse Document Frequency).
5.  **Similarity:** Cosine Similarity.

In [3]:
import os
import math
import pandas as pd
import numpy as np
import PyPDF2
import docx
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
from Sastrawi.StopWordRemover.StopWordRemoverFactory import StopWordRemoverFactory
import re

# Display settings for pandas to ensure we see the full tables
pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)

print("Libraries imported successfully.")

Libraries imported successfully.


In [4]:
def read_txt(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        return f.read()

def read_pdf(file_path):
    text = ""
    try:
        with open(file_path, 'rb') as f:
            reader = PyPDF2.PdfReader(f)
            for page in reader.pages:
                text += page.extract_text() + " "
    except Exception as e:
        print(f"Error reading PDF {file_path}: {e}")
    return text

def read_docx(file_path):
    try:
        doc = docx.Document(file_path)
        return " ".join([para.text for para in doc.paragraphs])
    except Exception as e:
        print(f"Error reading DOCX {file_path}: {e}")
        return ""

def load_documents(base_path):
    documents = [] # List of dictionaries: {'filename': name, 'content': text}
    
    # Map extensions to reading functions and subfolders
    loaders = {
        'texts': ('.txt', read_txt),
        'pdf': ('.pdf', read_pdf),
        'doc': ('.docx', read_docx)
    }

    for folder, (ext, loader_func) in loaders.items():
        folder_path = os.path.join(base_path, folder)
        if not os.path.exists(folder_path):
            print(f"Warning: Folder {folder_path} does not exist. Skipping.")
            continue
            
        for filename in os.listdir(folder_path):
            if filename.endswith(ext):
                filepath = os.path.join(folder_path, filename)
                content = loader_func(filepath)
                documents.append({'filename': filename, 'content': content})
                print(f"Loaded: {filename}")
                
    return pd.DataFrame(documents)

# --- DUMMY DATA GENERATION (Run this once if you don't have real files yet) ---
# Uncomment below lines to create dummy files for testing
# os.makedirs('dataset/texts', exist_ok=True)
# with open('dataset/texts/doc1.txt', 'w') as f: f.write("Kucing itu sedang tidur di meja.")
# with open('dataset/texts/doc2.txt', 'w') as f: f.write("Saya suka belajar pemrograman Python.")
# with open('dataset/texts/doc3.txt', 'w') as f: f.write("Kucing dan anjing bermain di taman.")
# ------------------------------------------------------------------------------

# Load the data
print("--- Loading Documents ---")
df_docs = load_documents('dataset - Copy') 
display(df_docs)

--- Loading Documents ---
Loaded: 1.txt
Loaded: 10.txt
Loaded: 11.txt
Loaded: 12.txt
Loaded: 13.txt
Loaded: 14.txt
Loaded: 15.txt
Loaded: 16.txt
Loaded: 17.txt
Loaded: 18.txt
Loaded: 19.txt
Loaded: 2.txt
Loaded: 20.txt
Loaded: 3.txt
Loaded: 4.txt
Loaded: 5.txt
Loaded: 6.txt
Loaded: 7.txt
Loaded: 8.txt
Loaded: 9.txt
Loaded: 152023193_Moh Ilyas_IMK_P2.pdf
Loaded: 2_Tugas_2-IFB354-1520193[1].pdf
Loaded: 4. RTM_2.pdf
Loaded: AAA RADIUS.pdf
Loaded: AKT298B-15-2023-193.pdf
Loaded: api (1).pdf
Loaded: api.pdf
Loaded: betates.pdf
Loaded: CV Moh Ilyas.pdf
Loaded: D1-D6.pdf
Loaded: 1.docx
Loaded: Alamat akhir ram.docx
Loaded: Api.docx
Loaded: BAB 1 PENDAHULUAN.docx
Loaded: basis data 2.docx
Loaded: basisdata_chap7.docx
Loaded: basisdata_chap8.docx
Loaded: CHAPTER 4_BASIS DATA.docx
Loaded: ciporeat.docx
Loaded: Doc1.docx


filename                                            content
0                             1.txt  aku takut tidak akan pernah bisa mengatasi sem...
1                            10.txt  favorit saya dari dulu selalu ribs barbeque di...
2                            11.txt  kebetulan juga media media yang semasa pak say...
3                            12.txt  [USERNAME] [USERNAME] Alhamdulillah, indonesia...
4                            13.txt  tidak habis pikir kenapa alatalat hobiku selal...
5                            14.txt  prediksi persija jakarta vs psis semarang 18 s...
6                            15.txt  tempat strategis , halaman luas , tetapi jumla...
7                            16.txt           saya sih cinta banget produk indonesia .
8                            17.txt  marah banget karena banyak karakter di buku in...
9                            18.txt  mister . ini mahal karena makanan ini makanan ...
10                           19.txt  aku yakin hubungan kita akan terus tumbuh kare...
11                            2.txt  amin amin mba dew :) sudah lama sekali tidak-m...
12                           20.txt  sebentar-sebentar itu bos lu kok ikut menyalak...
13                            3.txt  kalau sudah watak pembohong , sulit untuk dina...
14                            4.txt  Saat kita membenci sesuatu dg berlebihan dan m...
15                            5.txt  takut banget kalau kesempatan besar lewat begi...
16                            6.txt  marah banget karena keinginan ini seperti tida...
17                            7.txt  aku percaya bahwa kita bisa saling melengkapi ...
18                            8.txt  makanan nya mahal mahal , dan masakan nya kura...
19                            9.txt  setiap detik bersamamu membuatku semakin yakin...
20   152023193_Moh Ilyas_IMK_P2.pdf  Nama: Moh Ilyas  \nNRP: 152023193  \nLink: htt...
21  2_Tugas_2-IFB354-1520193[1].pdf  IFB-354 Bisnis Intelijen  \n \nAnalisis Data I...
22                     4. RTM_2.pdf   \nINSTITUT TEKNOLOGI NASIONAL  \nFAKULTAS  TE...
23                   AAA RADIUS.pdf  Nama: Moh Ilyas \nNRP: 152023193 \nTUGAS RADIU...
24          AKT298B-15-2023-193.pdf  ** DAFTAR NILAI MAHASISWA **\nSemester :GENAP ...
25                      api (1).pdf  Nama: Moh Ilyas \nNRP: 152023193 \nPentest api...
26                          api.pdf  Nama: Moh Ilyas \nNRP: 152023193 \nPentest api...
27                      betates.pdf  Nama:  Moh Ilyas  \nNRP: 152023193  \nBETA TES...
28                 CV Moh Ilyas.pdf  Moh Ilyas  \nBandung, Jawa Barat  | 0856243594...
29                        D1-D6.pdf  29 \n D. MENINGKATKAN KUALITA S CITRA -OPERASI...
30                           1.docx  1.3. Pendekatan Database  Pendekatan berbasis ...
31            Alamat akhir ram.docx  - Alamat akhir ram Alamat awal = C000h Alamat ...
32                         Api.docx  Password suppabase: FIT@JOURNAL!@# Lokasi Aqi/...
33           BAB 1 PENDAHULUAN.docx  BAB 1 PENDAHULUAN Latar Belakang Kemacetan lal...
34                basis data 2.docx  Tugas MK. IFB-104 Basis data TA 2023-2024  Ran...
35             basisdata_chap7.docx  Nama\t\t: NAUFAL AHMAD FAUZAN Kelas\t\t: EE Nr...
36             basisdata_chap8.docx  Nama\t\t: NAUFAL AHMAD FAUZAN Kelas\t\t: EE Nr...
37        CHAPTER 4_BASIS DATA.docx  CHAPTER 4 Aljabar Relasional dan Kalkulus Rela...
38                    ciporeat.docx  Nama: Moh Ilyas OUTCOME MENGIKUTI PEMATERIAN A...
39                        Doc1.docx

In [5]:
# Initialize Sastrawi tools
factory = StemmerFactory()
stemmer = factory.create_stemmer() # ECS Algorithm
stop_factory = StopWordRemoverFactory()
stopword_remover = stop_factory.create_stop_word_remover()

def preprocess(text, verbose=False):
    # 1. Case Folding
    text_lower = text.lower()
    
    # 2. Cleaning (Remove numbers and punctuation)
    text_clean = re.sub(r'[^a-z\s]', '', text_lower)
    
    # 3. Stopword Removal
    text_stop = stopword_remover.remove(text_clean)
    
    # 4. Stemming (ECS)
    text_stemmed = stemmer.stem(text_stop)
    
    # 5. Tokenization
    tokens = text_stemmed.split()
    
    if verbose:
        print(f"Original: {text[:50]}...")
        print(f"Case Folding: {text_lower[:50]}...")
        print(f"Stopword Removal: {text_stop[:50]}...")
        print(f"Stemming (ECS): {text_stemmed[:50]}...")
        print(f"Tokens: {tokens}")
        print("-" * 30)
        
    return tokens

print("--- Testing Preprocessing on First Document ---")
# Test on the first document to show the "Explainable" requirement
if not df_docs.empty:
    sample_tokens = preprocess(df_docs.iloc[0]['content'], verbose=True)

--- Testing Preprocessing on First Document ---
Original: aku takut tidak akan pernah bisa mengatasi semua i...
Case Folding: aku takut tidak akan pernah bisa mengatasi semua i...
Stopword Removal: aku takut akan pernah mengatasi semua dan menemuka...
Stemming (ECS): aku takut akan pernah atas semua dan temu jalan ke...
Tokens: ['aku', 'takut', 'akan', 'pernah', 'atas', 'semua', 'dan', 'temu', 'jalan', 'keluar']
------------------------------


In [6]:
from tqdm.notebook import tqdm  # Import progress bar specifically for Jupyter

# Create a place to store tokens
tokens_list = []

print("--- Starting Preprocessing Pipeline ---")

# Iterate through the DataFrame with a progress bar
# total=len(df_docs) tells the bar when to finish
for index, row in tqdm(df_docs.iterrows(), total=len(df_docs), desc="Processing Files"):
    
    filename = row['filename']
    file_type = filename.split('.')[-1].upper() # Get extension (PDF, DOCX, TXT)
    
    # Optional: Print current status (updates in real time)
    # logic to print only every 5 files or if it's a large file can be added here
    # but for 60 files, printing every file is okay.
    print(f"[{file_type}] Processing: {filename}...", end='\r')
    
    # Apply the preprocessing
    processed_tokens = preprocess(row['content'])
    tokens_list.append(processed_tokens)

print("\n--- Processing Complete! ---")

# Assign the results back to the DataFrame
df_docs['tokens'] = tokens_list

# Show preview
display(df_docs[['filename', 'tokens']].head())

--- Starting Preprocessing Pipeline ---


Processing Files:   0%|          | 0/40 [00:00<?, ?it/s]

[DOCX] Processing: Doc1.docx...x...DATA.docx...df...
--- Processing Complete! ---


filename                                             tokens
0    1.txt  [aku, takut, akan, pernah, atas, semua, dan, t...
1   10.txt  [favorit, dari, dulu, selalu, ribs, barbeque, ...
2   11.txt  [betul, media, media, masa, pak, say, dulu, mi...
3   12.txt  [username, username, alhamdulillah, indonesia,...
4   13.txt  [habis, pikir, alatalat, hobi, selalu, cepat, ...

In [7]:
# 1. Create Vocabulary (Unique Terms)
all_tokens = [token for sublist in df_docs['tokens'] for token in sublist]
vocabulary = sorted(list(set(all_tokens)))

print(f"Vocabulary Size: {len(vocabulary)}")
print(f"Vocabulary Sample: {vocabulary[:10]}")

# 2. Term Frequency (TF) Table
# We use Raw Count for this example
tf_data = []
for doc_tokens in df_docs['tokens']:
    doc_tf_vector = []
    for term in vocabulary:
        doc_tf_vector.append(doc_tokens.count(term))
    tf_data.append(doc_tf_vector)

df_tf = pd.DataFrame(tf_data, columns=vocabulary, index=df_docs['filename'])

print("\n--- Term Frequency (TF) Table ---")
display(df_tf)

# 3. Inverse Document Frequency (IDF)
# Formula: log10(Total Documents / Document Frequency of term)
N = len(df_docs)
idf_data = []

for term in vocabulary:
    # Count how many documents contain this term
    df_count = sum([1 for tokens in df_docs['tokens'] if term in tokens])
    
    # Calculate IDF (adding 1 to df_count to avoid division by zero if necessary)
    idf_val = math.log10(N / (df_count)) if df_count > 0 else 0
    idf_data.append(idf_val)

df_idf = pd.DataFrame([idf_data], columns=vocabulary, index=['IDF'])

print("\n--- Inverse Document Frequency (IDF) ---")
display(df_idf)

# 4. TF-IDF Matrix
# Formula: TF * IDF
df_tfidf = df_tf.mul(df_idf.iloc[0], axis=1)

print("\n--- TF-IDF Matrix ---")
display(df_tfidf)

Vocabulary Size: 2558
Vocabulary Sample: ['a', 'aaa', 'ab', 'abstraksi', 'abu', 'abur', 'acara', 'access', 'achieved', 'action']

--- Term Frequency (TF) Table ---


a  aaa  ab  abstraksi  abu  abur  acara  access  achieved  action  actionfilter  acu  ada  adalah  adaptasi  adaptif  adapun  admin  administrasi  administratif  administrator  administrators  adobe  adopsi  adp  adzdzariyat  agam  agama  agar  agement  aggregate  aggregatefunction  aggregation  agregasi  agregat  agus  ah  ahmad  ahmadusman  ai  aimageikjl  air  airpollution  airquality  ajar  aju  akal  akan  akar  akhir  akibat  akidah  akrab  akses  aksesibilitas  aksi  aktb  aktif  aktivitas  aktual  aku  akuisisi  akurat  al  ala  alah  alam  alamat  alami  alas  alat  alatalat  alfabet  algebra  algoritma  algoritmikinformatikabandung  alhamdulillah  alihalih  alir  alis  aljabar  allah  allocation  almat  alokasi  alquran  alter  alternatif  alur  ama  amal  aman  amanah  amat  amazon  ambigu  ambil  amelia  american  amin  ampu  ampun  an  anak  anal  analis  analisis  analitik  analysis  analytical  analytics  and  anda  andal  andi  \
filename                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         
1.txt                             0    0   0          0    0     0      0       0         0       0             0    0    0       0         0        0       0      0             0              0              0               0      0       0    0            0     0      0     0        0          0                  0            0         0        0     0   0      0           0   0           0    0             0           0     0    0     0     1     0      0       0       0      0      0              0     0     0      0          0       0    1         0       0   0    0     0     0       0      0     0     0         0        0        0          0                             0              0         0     0     0        0      0           0      0        0        0      0           0     0    0     0     0       0     0       0       0      0       0         0     0     0      0   0     0     0       0         0         0         0           0          0    0     0      0     0   
10.txt                            0    0   0          0    0     0      0       0         0       0             0    0    0       0         0        0       0      0             0              0              0               0      0       0    0            0     0      0     0        0          0                  0            0         0        0     0   0      0           0   0           0    1             0           0     0    0     0     0     0      0       0       0      0      0              0     0     0      0          0       0    0         0       0   0    0     0     0       0      0     0     0         0        0        0          0                             0              0         0     0     0        0      0           0      0        0        0      0           0     0    0     0     0       0     0       0       0      0       0         0     0     0      0   0     0     0       0         0         0         0           0          0    0     0      0     0   
11.txt                            0    0   0          0   


--- Inverse Document Frequency (IDF) ---


a      aaa       ab  abstraksi      abu     abur    acara  access  achieved   action  actionfilter      acu      ada   adalah  adaptasi  adaptif   adapun    admin  administrasi  administratif  administrator  administrators    adobe    adopsi      adp  adzdzariyat     agam    agama     agar  agement  aggregate  aggregatefunction  aggregation  agregasi   agregat     agus       ah    ahmad  ahmadusman       ai  aimageikjl      air  airpollution  airquality     ajar      aju     akal     akan     akar    akhir   akibat   akidah    akrab     akses  aksesibilitas     aksi     aktb     aktif  aktivitas   aktual      aku  akuisisi   akurat       al      ala     alah      alam   alamat  alami     alas  alat  alatalat  alfabet  algebra  algoritma  algoritmikinformatikabandung  alhamdulillah  alihalih     alir     alis  aljabar    allah  allocation    almat  alokasi  alquran    alter  alternatif      alur      ama     amal  aman   amanah     amat   amazon   ambigu    ambil   amelia  \
IDF  0.647817  1.60206  1.60206    1.60206  1.60206  1.60206  1.60206     1.0   1.60206  1.30103       1.60206  1.30103  0.69897  0.69897   1.60206  1.60206  1.60206  1.60206       1.30103        1.60206        1.60206         1.30103  1.60206  1.124939  1.60206      1.60206  1.30103  1.30103  1.30103  1.60206    1.60206            1.60206      1.60206       1.0  1.124939  1.60206  1.60206  1.30103     1.60206  1.30103     1.60206  1.30103       1.60206     1.60206  1.30103  1.60206  1.60206  0.60206  1.60206  0.69897  1.30103  1.60206  1.60206  0.823909        1.60206  1.60206  1.60206  1.124939    1.30103  1.60206  0.90309   1.60206  1.30103  1.60206  1.60206  1.60206  1.124939  1.30103    1.0  1.60206   1.0   1.60206  1.60206  1.60206    1.30103                       1.60206        1.30103   1.60206  1.60206  1.30103  1.60206  1.30103     1.60206  1.60206  1.60206  1.60206  1.60206     1.30103  1.124939  1.60206  1.60206   1.0  1.60206  1.60206  1.60206  1.60206  0.69897  1.60206   

     american     amin     ampu    ampun        an     anak     anal   analis  analisis  analitik  analysis  analytical  analytics  and     anda  andal     andi   anggap   anggar  anggota    angka      ann   anonim  anposisi  ansisparc     antar   antara  antarmuka  antarwilayah  anticipation    antre       ap       apa     apan  api     apit  aplikasi  aplikasinoseq   apollo   aporan   applet  application  applications  applicationserver  appnoseq  approach    april      aqi  aqicuaca      arah     arat  architektur      are     area    arena  argumen  aritmatika    array    arsip    arsir  arsitek  arsitektur  arti  artikel     arus      asa     asal     aset   ashari      asi    asing  asli      asm  asosiasi     aspek  assigned  assignment   assist   asumsi     atan     atas      atau     aten     atom  atribut  atributatribut      atur    audio    audit  autolookup  autonumber      avg  aviation     awal      aws     axik     ayat         b       ba      bab      baca  backend  \
IDF   1.60206  1.60206  1.60206  1.60206  1.124939  1.60206  1.60206  0.90309  0.823909   1.60206   1.60206     1.30103    1.60206  1.0  1.60206    1.0  1.60206  1.60206  1.30103      1.0  1.30103  1.60206  1.30103   1.60206    1.60206  1.124939  1.30103    1.30103       1.60206       1.60206  1.60206  1.60206  0.823909  1.60206  1.0  1.60206  0.756962        1.60206  1.60206  1.60206  1.60206      1.60206       1.60206            1.60206   1.60206   1.60206  1.60206  1.60206   1.60206  1.124939  1.60206      1.60206  1.60206  0.90309  1.60206  1.30103     1.30103  1.60206  1.30103  1.60206  1.60206         1.0   1.0  1.60206  1.60206  1.60206  1.30103  1.60206  1.60206  1.60206  1.30103   1.0  1.60206   1.30103  1.124939   1.60206     1.60206  1.60206  1.30103  1.60206  0.60206  1.124939  1.60206  1.60206      1.0         1.60206  0.756962  1.60206  1.30103     1.60206     1.60206  1.60206   1.60206  0.90309  1.60206  1.60206  1.60206  0.823909  1.60206  0.90309  0.756962  1.60206   

     bac


--- TF-IDF Matrix ---


a      aaa      ab  abstraksi      abu     abur    acara  access  achieved   action  actionfilter      acu      ada   adalah  adaptasi  adaptif   adapun    admin  administrasi  administratif  administrator  administrators    adobe    adopsi      adp  adzdzariyat     agam    agama     agar  agement  aggregate  aggregatefunction  aggregation  agregasi   agregat     agus       ah    ahmad  ahmadusman        ai  aimageikjl      air  airpollution  airquality     ajar      aju     akal     akan     akar    akhir   akibat   akidah    akrab      akses  aksesibilitas     aksi     aktb     aktif  aktivitas   aktual      aku  akuisisi   akurat       al      ala     alah      alam   alamat  alami     alas  alat  alatalat  alfabet  algebra  algoritma  algoritmikinformatikabandung  alhamdulillah  alihalih     alir     alis   aljabar    allah  allocation    almat   alokasi  alquran    alter  alternatif      alur      ama     amal  aman   amanah     amat  \
filename                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
1.txt                             0.000000  0.00000  0.0000    0.00000  0.00000  0.00000  0.00000     0.0   0.00000  0.00000       0.00000  0.00000  0.00000  0.00000   0.00000  0.00000  0.00000  0.00000       0.00000        0.00000        0.00000         0.00000  0.00000  0.000000  0.00000      0.00000  0.00000  0.00000  0.00000  0.00000    0.00000            0.00000      0.00000       0.0  0.000000  0.00000  0.00000  0.00000     0.00000   0.00000     0.00000  0.00000       0.00000     0.00000  0.00000  0.00000  0.00000  0.60206  0.00000  0.00000  0.00000  0.00000  0.00000   0.000000        0.00000  0.00000  0.00000  0.000000    0.00000  0.00000  0.90309   0.00000  0.00000  0.00000  0.00000  0.00000  0.000000  0.00000    0.0  0.00000   0.0   0.00000  0.00000  0.00000    0.00000                       0.00000        0.00000   0.00000  0.00000  0.00000   0.00000  0.00000     0.00000  0.00000   0.00000  0.00000  0.00000     0.00000  0.000000  0.00000  0.00000   0.0  0.00000  0.00000   
10.txt                            0.000000  0.00000  0.0000    0.00000  0.00000  0.00000  0.00000     0.0   0.00000  0.00000       0.00000  0.00000  0.00000  0.00000   0.00000  0.00000  0.00000  0.00000       0.00000        0.00000        0.00000         0.00000  0.00000  0.000000  0.00000      0.00000  0.00000  0.00000  0.00000  0.00000    0.00000            0.00000      0.00000       0.0  0.000000  0.00000  0.00000  0.00000     0.00000   0.00000     0.00000  1.30103       0.00000     0.00000  0.00000  0.00000  0.00000  0.00000  0.00000  0.00000  0.00000  0.00000  0.00000   0.000000        0.00000  0.00000  0.00000  0.000000    0.00000  0.00000  0.00000   0.00000  0.00000  0.00000  0.00000  0.00000  0.000000  0.00000    0.0  0.00000   0.0   0.00000  0.00000  0.00000    0.00000                       0.00000        0.00000   0.00000  0.00000  0.00000   0.00000  0.00000     0.00000  0.00000   0.00000  0.00000  0.00000     0.00000  0.000000  0.00000  0.00000   0.0  0.00000  0.00000   
11.txt                            0.000000  0.00000  

In [16]:
def process_query(query, vocabulary, df_idf):
    # 1. Preprocess Query
    print(f"\nQuery: {query}")
    query_tokens = preprocess(query, verbose=False)
    print(f"Query Tokens: {query_tokens}")
    
    # 2. Calculate Query TF
    query_tf = []
    for term in vocabulary:
        query_tf.append(query_tokens.count(term))
        
    # 3. Calculate Query TF-IDF
    # We use the IDF from the document corpus
    query_tfidf = np.array(query_tf) * df_idf.iloc[0].values
    
    return query_tfidf

def cosine_similarity(vec_a, vec_b):
    # Formula: (A . B) / (||A|| * ||B||)
    dot_product = np.dot(vec_a, vec_b)
    norm_a = np.linalg.norm(vec_a)
    norm_b = np.linalg.norm(vec_b)
    
    if norm_a == 0 or norm_b == 0:
        return 0.0
        
    return dot_product / (norm_a * norm_b)

# --- EXECUTE RETRIEVAL ---

# Define a search query
query = "KUALITA "  # Change this to test different queries

# Process Query
query_vector = process_query(query, vocabulary, df_idf)

# Calculate Similarity with all documents
results = []
for filename, doc_vector in df_tfidf.iterrows():
    sim_score = cosine_similarity(query_vector, doc_vector.values)
    results.append({'filename': filename, 'similarity': sim_score})

# Create Results DataFrame
df_results = pd.DataFrame(results)

# Rank Documents (Sort by similarity descending)
df_results = df_results.sort_values(by='similarity', ascending=False)

print("\n--- Ranked Retrieval Results ---")
display(df_results)


Query: KUALITA 
Query Tokens: ['kualita']

--- Ranked Retrieval Results ---


filename  similarity
29                        D1-D6.pdf    0.013278
0                             1.txt    0.000000
1                            10.txt    0.000000
22                     4. RTM_2.pdf    0.000000
23                   AAA RADIUS.pdf    0.000000
24          AKT298B-15-2023-193.pdf    0.000000
25                      api (1).pdf    0.000000
26                          api.pdf    0.000000
27                      betates.pdf    0.000000
28                 CV Moh Ilyas.pdf    0.000000
30                           1.docx    0.000000
31            Alamat akhir ram.docx    0.000000
32                         Api.docx    0.000000
33           BAB 1 PENDAHULUAN.docx    0.000000
34                basis data 2.docx    0.000000
35             basisdata_chap7.docx    0.000000
36             basisdata_chap8.docx    0.000000
37        CHAPTER 4_BASIS DATA.docx    0.000000
38                    ciporeat.docx    0.000000
21  2_Tugas_2-IFB354-1520193[1].pdf    0.000000
20   152023193_Moh Ilyas_IMK_P2.pdf    0.000000
19                            9.txt    0.000000
9                            18.txt    0.000000
2                            11.txt    0.000000
3                            12.txt    0.000000
4                            13.txt    0.000000
5                            14.txt    0.000000
6                            15.txt    0.000000
7                            16.txt    0.000000
8                            17.txt    0.000000
10                           19.txt    0.000000
18                            8.txt    0.000000
11                            2.txt    0.000000
12                           20.txt    0.000000
13                            3.txt    0.000000
14                            4.txt    0.000000
15                            5.txt    0.000000
16                            6.txt    0.000000
17                            7.txt    0.000000
39                        Doc1.docx    0.000000